# Daten Extraktion aus dem Bundesanzeiger

## Vorbereitung

In [255]:
import pandas as pd

from aki_prj23_transparenzregister.utils.data_extraction.bundesanzeiger import (
    Bundesanzeiger,
)

ba_wrapper = Bundesanzeiger()
# df_reports = ba_wrapper.get_information("Törmer Energy Solar 1 GmbH & Co. KG", "")
# df_reports = ba_wrapper.get_information("Atos IT-Dienstleistung und Beratung GmbH", "")
df_reports = ba_wrapper.get_information(
    "Stadtwerke Haltern am See Gesellschaft mit beschränkter Haftung", ""
)
df_reports.head()

date                                            company  \
1 2022-10-21  Stadtwerke Haltern am See Gesellschaft mit bes...   
3 2021-10-12  Stadtwerke Haltern am See Gesellschaft mit bes...   
5 2020-12-03  Stadtwerke Haltern am See Gesellschaft mit bes...   
6 2020-01-09  Stadtwerke Haltern am See Gesellschaft mit bes...   
7 2019-10-10  Stadtwerke Haltern am See Gesellschaft mit bes...   

                                          raw_report  jahr  \
1  <div class="publication_container">\n <div cla...  2021   
3  <div class="publication_container">\n <div cla...  2020   
5  <div class="publication_container">\n <div cla...  2019   
6  <div class="publication_container">\n <div cla...  2018   
7  <div class="publication_container">\n <div cla...  2017   

                                            auditors  \
1  [Auditor(name='Volker Voelcker', company='Pric...   
3  [Auditor(name='Hubert Ahlers', company='Pricew...   
5  [Auditor(name='Hubert Ahlers', company='Pricew...   
6  [Auditor(name='Hubert Ahlers', company='Pricew...   
7                                                 []   

                                   financial_results  
1  {'revenue': 46275.0, 'net_income': 1757.0, 'eb...  
3  {'revenue': 47459.0, 'net_income': 1661.0, 'eb...  
5  {'revenue': 45575.0, 'net_income': 1599.0, 'eb...  
6  {'revenue': 43898.0, 'net_income': 2043.0, 'eb...  
7                                                 {}

## Daten Extraktion

In [256]:
from bs4 import BeautifulSoup
from io import StringIO

In [257]:
sample_report = df_reports.iloc[1].raw_report

### Aufsichtsrat

**TODO**

### Bilanz bzw. GuV

In [258]:
def parse_tables(report: str) -> list:
    result = []
    soup = BeautifulSoup(report, features="html.parser")
    for table in soup.find_all("table", {"class": "std_table"}):
        df = pd.read_html(StringIO(str(table)), flavor="bs4")[0]
        print(df.columns)
        print(df.dtypes)
        result.append(df)
    return result


tables = parse_tables(sample_report)

MultiIndex([('Unnamed: 0_level_0', 'Unnamed: 0_level_1'),
            (              '2020',                 'T€'),
            (              '2019',                 'T€'),
            (       'Veränderung',                 'T€'),
            (       'Veränderung',                  '%')],
           )
Unnamed: 0_level_0  Unnamed: 0_level_1     object
2020                T€                    float64
2019                T€                    float64
Veränderung         T€                      int64
                    %                       int64
dtype: object
MultiIndex([('Unnamed: 0_level_0', 'Unnamed: 0_level_1'),
            (              '2020',                 'T€'),
            (              '2020',                  '%'),
            (              '2019',                 'T€'),
            (              '2019',                  '%'),
            (     'Veränderungen',                 'T€'),
            (     'Veränderungen',                  '%')],
           )
Unnamed: 0_l

In [259]:
current_table = tables[0]
current_table.head()

Unnamed: 0_level_0     2020     2019 Veränderung     
                       Unnamed: 0_level_1       T€       T€          T€    %
0       Jahresüberschuss/Jahresfehlbetrag    1.661    1.599          62   39
1  + Steuern vom Einkommen und vom Ertrag  796.000  792.000           4    5
2                                   = EBT    2.457    2.391          66   28
3                        + Finanzergebnis  -13.000  -99.000          86 -869
4                                  = EBIT    2.444    2.292         152   66

In [260]:
import re


def cleanse_string(value: str) -> str:
    if value is not None and isinstance(value, str):
        return re.sub(r"(.+\.).", "", value)
    return None

In [261]:
for index, row in current_table.iterrows():
    current_table.iloc[index][0] = cleanse_string(row[0])
current_table.head()

C:\Users\trist\AppData\Local\Temp\ipykernel_24300\152097142.py:2: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  current_table.iloc[index][0] = cleanse_string(row[0])
C:\Users\trist\AppData\Local\Temp\ipykernel_24300\152097142.py:2: FutureWarning: Series.__setitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To set a value by position, use `ser.iloc[pos] = value`
  current_table.iloc[index][0] = cleanse_string(row[0])


Unnamed: 0_level_0     2020     2019 Veränderung     
                       Unnamed: 0_level_1       T€       T€          T€    %
0       Jahresüberschuss/Jahresfehlbetrag    1.661    1.599          62   39
1  + Steuern vom Einkommen und vom Ertrag  796.000  792.000           4    5
2                                   = EBT    2.457    2.391          66   28
3                        + Finanzergebnis  -13.000  -99.000          86 -869
4                                  = EBIT    2.444    2.292         152   66

In [262]:
def parse_string_to_float(value) -> float:
    try:
        if value is None:
            return None
        # if isinstance(value, float):
        # return value
        return float(str(value).replace(".", "").replace(",", "."))
    except Exception as e:
        return None


def apply_factor(value, factor: float):
    transformed_value = parse_string_to_float(value)
    if transformed_value is None or isinstance(transformed_value, str):
        return None
    result = transformed_value * factor
    # print(result)
    return result

In [263]:
converter = {
    "Mio€": 1 * 10**6,
    "Mio": 1 * 10**6,
    "T€": 1 * 10**3,
    "TEUR": 1 * 10**3,
    "EUR": 1,
    "€": 1,
}

for column in current_table.columns[1:]:
    if isinstance(column, tuple):
        for c in column:
            for x, factor in converter.items():
                if x in c:
                    current_table[column] = current_table[column].apply(
                        lambda x: apply_factor(x, factor)
                    )
                    break
    else:
        for x, factor in converter.items():
            parts = str(column).split(" ")
            for y in parts:
                if re.match(x, y):
                    current_table[column] = current_table[column].apply(
                        lambda x: apply_factor(x, factor)
                    )
                    current_table.rename({column: parts[0]}, inplace=True, axis=1)
                    break

current_table.dropna(axis=0, how="all", inplace=True)
current_table.dropna(axis=1, how="all", inplace=True)
current_table.head()

Unnamed: 0_level_0       2020       2019 Veränderung  \
                       Unnamed: 0_level_1         T€         T€          T€   
0       Jahresüberschuss/Jahresfehlbetrag  1661000.0  1599000.0     62000.0   
1  + Steuern vom Einkommen und vom Ertrag  7960000.0  7920000.0      4000.0   
2                                   = EBT  2457000.0  2391000.0     66000.0   
3                        + Finanzergebnis  -130000.0  -990000.0     86000.0   
4                                  = EBIT  2444000.0  2292000.0    152000.0   

        
     %  
0   39  
1    5  
2   28  
3 -869  
4   66

In [264]:
current_table.dtypes

Unnamed: 0_level_0  Unnamed: 0_level_1     object
2020                T€                    float64
2019                T€                    float64
Veränderung         T€                    float64
                    %                       int64
dtype: object

In [265]:
# Remove columns hosting non-numerics; excl. first column hosting keys
columns_to_prune = []
for column_index, column_type in enumerate(current_table.dtypes[1:]):
    if column_type in ["object", "str"]:
        columns_to_prune.append(column_index + 1)

current_table = current_table.drop(
    current_table.columns[columns_to_prune], axis="columns"
)

In [266]:
# Prune rows where first columns is None
import numpy as np

current_table = current_table.replace(to_replace="None", value=np.nan).dropna()
current_table

Unnamed: 0_level_0       2020       2019 Veränderung  \
                       Unnamed: 0_level_1         T€         T€          T€   
0       Jahresüberschuss/Jahresfehlbetrag  1661000.0  1599000.0     62000.0   
1  + Steuern vom Einkommen und vom Ertrag  7960000.0  7920000.0      4000.0   
2                                   = EBT  2457000.0  2391000.0     66000.0   
3                        + Finanzergebnis  -130000.0  -990000.0     86000.0   
4                                  = EBIT  2444000.0  2292000.0    152000.0   
5                  + Abschreibungsaufwand  2239000.0  2273000.0    -34000.0   
6                                = EBITDA  4683000.0  4565000.0    118000.0   

        
     %  
0   39  
1    5  
2   28  
3 -869  
4   66  
5  -15  
6   26

In [267]:
exps = [r"^[0-9a-zA-Z]+[\.\)] ", r"[\+\=\-\_]"]
for _index, row in current_table.iterrows():
    for exp in exps:
        # print(row[0])
        row[0] = re.sub(exp, "", row[0]).strip()
        # print(row[0])

C:\Users\trist\AppData\Local\Temp\ipykernel_24300\1758297134.py:8: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  row[0] = re.sub(exp, '', row[0]).strip()
C:\Users\trist\AppData\Local\Temp\ipykernel_24300\1758297134.py:8: FutureWarning: Series.__setitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To set a value by position, use `ser.iloc[pos] = value`
  row[0] = re.sub(exp, '', row[0]).strip()


In [268]:
kpis = {}

exps = [r"^[0-9a-zA-Z]+[\.\)] ", r"[\+\=\-\_]"]
for _index, row in current_table.iterrows():
    name_cleansed = row[0]
    for exp in exps:
        # print(row[0])
        name_cleansed = re.sub(exp, "", name_cleansed).strip()
    kpis[name_cleansed] = row[1]
kpis

C:\Users\trist\AppData\Local\Temp\ipykernel_24300\2923576447.py:8: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  name_cleansed = row[0]
C:\Users\trist\AppData\Local\Temp\ipykernel_24300\2923576447.py:12: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  kpis[name_cleansed] = row[1]


{'Jahresüberschuss/Jahresfehlbetrag': 1661000.0,
 'Steuern vom Einkommen und vom Ertrag': 7960000.0,
 'EBT': 2457000.0,
 'Finanzergebnis': -130000.0,
 'EBIT': 2444000.0,
 'Abschreibungsaufwand': 2239000.0,
 'EBITDA': 4683000.0}